In [0]:
dbutils.fs.ls("/mnt/raw")


[FileInfo(path='dbfs:/mnt/raw/bronze/', name='bronze/', size=0, modificationTime=1763725478000),
 FileInfo(path='dbfs:/mnt/raw/demand_data/', name='demand_data/', size=0, modificationTime=1763708940000),
 FileInfo(path='dbfs:/mnt/raw/external_factors/', name='external_factors/', size=0, modificationTime=1763715906000),
 FileInfo(path='dbfs:/mnt/raw/feature_engineering/', name='feature_engineering/', size=0, modificationTime=1763708878000)]

In [0]:
# ====================================================
# 1. IMPORTS + PATHS
# ====================================================
from pyspark.sql.functions import *
from pyspark.sql.types import *

bronze_path = "/mnt/raw/bronze"
silver_path = "/mnt/raw/silver"

dbutils.fs.mkdirs(silver_path)

# ====================================================
# 2. READ FROM BRONZE
# ====================================================
demand_df = spark.read.format("delta").load(f"{bronze_path}/demand")
external_df = spark.read.format("delta").load(f"{bronze_path}/external")
feateng_df = spark.read.format("delta").load(f"{bronze_path}/feateng")

print("Bronze datasets loaded successfully!")

# ====================================================
# 3. NORMALIZATION FUNCTION (Fix Join Mismatches)
# ====================================================
from pyspark.sql.functions import regexp_replace

def normalize_region_service(df):
    return (
        df.withColumn("Region",
                      upper(trim(regexp_replace("Region", "[^A-Za-z ]", ""))))
          .withColumn("Service",
                      upper(trim(regexp_replace("Service", "[^A-Za-z ]", ""))))
    )

# ====================================================
# 4. CLEAN DEMAND DATA
# ====================================================
demand_clean = (
    demand_df
    .withColumn("Date", to_date("Date"))
    .transform(normalize_region_service)
    .dropDuplicates()
)

# ====================================================
# 5. CLEAN EXTERNAL DATA
# ====================================================
external_clean = (
    external_df
    .withColumn("Date", to_date("Date"))
    .dropDuplicates()
    .fillna({
        "Cloud_Demand_Index": 0,
        "GDP_Growth": 0.0,
        "Inflation": 0.0,
        "Competitor_Price_Index": 0
    })
)

# ====================================================
# 6. CLEAN FEATURE ENGINEERING DATA
# ====================================================
feateng_clean = (
    feateng_df
    .withColumn("Date", to_date("Date"))
    .transform(normalize_region_service)
    .dropDuplicates()
    .fillna(0)
)

# ====================================================
# 7. DROP ONLY TRUE DUPLICATE COLUMNS (safe)
# ====================================================
join_keys = {"Date", "Region", "Service"}

duplicate_cols = [
    c for c in feateng_clean.columns
    if c in demand_clean.columns and c not in join_keys
]

print("Dropping only real duplicate columns:", duplicate_cols)

feateng_clean = feateng_clean.drop(*duplicate_cols)

# ====================================================
# 8. OUTLIER CAPPING (SAFE)
# ====================================================
quant = demand_clean.approxQuantile("Daily_Usage_Units", [0.99], 0.05)[0]

demand_clean = demand_clean.withColumn(
    "Daily_Usage_Units",
    when(col("Daily_Usage_Units") > quant, quant)
    .otherwise(col("Daily_Usage_Units"))
)

# ====================================================
# 9. JOIN → FINAL SILVER MASTER
# ====================================================

# Step 1 -> Demand + External
demand_external = demand_clean.join(
    external_clean,
    on="Date",
    how="left"
)

# Step 2 -> Add Feature Engineering
silver_master = demand_external.join(
    feateng_clean,
    on=["Date", "Region", "Service"],
    how="left"
)

# ====================================================
# 10. VALIDATION
# ====================================================
print("Duplicate rows found:", silver_master.count() - silver_master.dropDuplicates().count())
silver_master.printSchema()
display(silver_master.limit(10))

# ====================================================
# 11. WRITE SILVER TABLE
# ====================================================
silver_master.write.format("delta") \
    .mode("overwrite") \
    .save(f"{silver_path}/master")

print("SILVER LAYER CREATED SUCCESSFULLY!")

# ====================================================
# 12. TEST READ
# ====================================================
display(
    spark.read.format("delta").load(f"{silver_path}/master")
)


Bronze datasets loaded successfully!
Dropping only real duplicate columns: ['Daily_Usage_Units', 'Peak_Usage_Units', 'VM_Count', 'Storage_TB', 'Season', 'Econ_Index', 'Downtime_Min']
Duplicate rows found: 0
root
 |-- Date: date (nullable = true)
 |-- Region: string (nullable = true)
 |-- Service: string (nullable = true)
 |-- Daily_Usage_Units: double (nullable = true)
 |-- Peak_Usage_Units: integer (nullable = true)
 |-- VM_Count: integer (nullable = true)
 |-- Storage_TB: integer (nullable = true)
 |-- Season: string (nullable = true)
 |-- Econ_Index: integer (nullable = true)
 |-- Downtime_Min: integer (nullable = true)
 |-- Cloud_Demand_Index: integer (nullable = true)
 |-- GDP_Growth: double (nullable = true)
 |-- Inflation: double (nullable = true)
 |-- Competitor_Price_Index: integer (nullable = true)
 |-- Usage_Lag_1: integer (nullable = true)
 |-- Usage_Lag_7: integer (nullable = true)
 |-- Week_Over_Week_Growth: double (nullable = true)
 |-- Seasonality_Factor: double (nullab

Date Region Service Daily_Usage_Units Peak_Usage_Units VM_Count Storage_TB Season Econ_Index Downtime_Min Cloud_Demand_Index GDP_Growth Inflation Competitor_Price_Index Usage_Lag_1 Usage_Lag_7 Week_Over_Week_Growth Seasonality_Factor 2020-01-03 WEST EUROPE COMPUTE 80231.0 88221 8478 0 Winter 96 3 89 2.910710224528352 5.363531613888448 93 119622 0 0.0 1.1941372778403934 2020-05-06 CENTRAL INDIA COMPUTE 152801.0 178906 7130 0 Spring 94 3 119 5.074715838791222 5.187429055730949 100 178140 159784 -4.370274871075953 1.071231507866667 2020-07-01 EAST US COMPUTE 71921.0 81785 10472 0 Summer 107 3 82 5.370439236321397 5.209181283430252 123 77560 167720 -57.11841163844503 1.1551871985050821 2020-07-13 EAST US COMPUTE 104660.0 123053 11518 0 Summer 91 0 81 5.503432483122108 6.665496819362889 126 76343 125647 -16.703144523944065 1.1132691804913937 2020-08-12 CENTRAL INDIA COMPUTE 73721.0 91507 14398 0 Summer 99 1 66 4.674224066499404 5.769263896822682 127 175947 73124 0.8164214211476397 1.1981467620302828 2020-10-11 WEST EUROPE STORAGE 0.0 0 0 647 Autumn 81 0 93 4.190859667788166 4.770330971779169 112 0 0 0.0 1.1132897652695177 2020-10-23 EAST US COMPUTE 120747.0 144550 3002 0 Autumn 99 0 107 5.11375325981645 4.248749307460542 91 151683 50445 139.36366339577756 1.1892668914935995 2020-11-06 WEST EUROPE COMPUTE 83890.0 104425 10411 0 Autumn 86 1 119 4.830710806907196 7.4308754230563165 114 110564 90631 -7.437852390462425 1.192496216502345 2020-12-07 WEST EUROPE COMPUTE 154081.0 182260 11277 0 Winter 108 2 75 5.89883861848111 6.764184071482227 96 144479 153874 0.13452565085719484 1.1472035677435046 2020-12-12 WEST EUROPE STORAGE 0.0 0 0 631 Winter 103 2 87 3.0602180182312395 3.6643202348234736 95 0 0 0.0 1.0916857030430658

SILVER LAYER CREATED SUCCESSFULLY!


Date Region Service Daily_Usage_Units Peak_Usage_Units VM_Count Storage_TB Season Econ_Index Downtime_Min Cloud_Demand_Index GDP_Growth Inflation Competitor_Price_Index Usage_Lag_1 Usage_Lag_7 Week_Over_Week_Growth Seasonality_Factor 2020-01-03 WEST EUROPE COMPUTE 80231.0 88221 8478 0 Winter 96 3 89 2.910710224528352 5.363531613888448 93 119622 0 0.0 1.1941372778403934 2020-05-06 CENTRAL INDIA COMPUTE 152801.0 178906 7130 0 Spring 94 3 119 5.074715838791222 5.187429055730949 100 178140 159784 -4.370274871075953 1.071231507866667 2020-07-01 EAST US COMPUTE 71921.0 81785 10472 0 Summer 107 3 82 5.370439236321397 5.209181283430252 123 77560 167720 -57.11841163844503 1.1551871985050821 2020-07-13 EAST US COMPUTE 104660.0 123053 11518 0 Summer 91 0 81 5.503432483122108 6.665496819362889 126 76343 125647 -16.703144523944065 1.1132691804913937 2020-08-12 CENTRAL INDIA COMPUTE 73721.0 91507 14398 0 Summer 99 1 66 4.674224066499404 5.769263896822682 127 175947 73124 0.8164214211476397 1.1981467620302828 2020-10-11 WEST EUROPE STORAGE 0.0 0 0 647 Autumn 81 0 93 4.190859667788166 4.770330971779169 112 0 0 0.0 1.1132897652695177 2020-10-23 EAST US COMPUTE 120747.0 144550 3002 0 Autumn 99 0 107 5.11375325981645 4.248749307460542 91 151683 50445 139.36366339577756 1.1892668914935995 2020-11-06 WEST EUROPE COMPUTE 83890.0 104425 10411 0 Autumn 86 1 119 4.830710806907196 7.4308754230563165 114 110564 90631 -7.437852390462425 1.192496216502345 2020-12-07 WEST EUROPE COMPUTE 154081.0 182260 11277 0 Winter 108 2 75 5.89883861848111 6.764184071482227 96 144479 153874 0.13452565085719484 1.1472035677435046 2020-12-12 WEST EUROPE STORAGE 0.0 0 0 631 Winter 103 2 87 3.0602180182312395 3.6643202348234736 95 0 0 0.0 1.0916857030430658 2020-12-29 CENTRAL INDIA STORAGE 0.0 0 0 792 Winter 106 0 65 4.130949398015879 3.3567364727340228 92 0 0 0.0 1.1076438595745872 2020-12-31 CENTRAL INDIA COMPUTE 165435.0 199558 3087 0 Winter 97 0 69 4.91721719566118 3.955447025457805 101 136026 84506 95.76716446169503 1.0870990642991987 2021-01-10 EAST US STORAGE 0.0 0 0 1095 Winter 108 2 84 2.119215670206506 5.051337039278507 114 0 0 0.0 1.192305139144724 2021-01-21 WEST EUROPE STORAGE 0.0 0 0 1178 Winter 85 3 103 3.099126224761219 7.486984197048588 116 0 0 0.0 1.1166131734210438 2021-02-06 EAST US COMPUTE 72398.0 83695 12155 0 Winter 90 1 68 2.7977631903837654 3.2932039360377607 113 89849 76901 -5.855580551618314 1.1993176399922538 2021-02-18 EAST US STORAGE 0.0 0 0 473 Winter 87 3 88 4.319278500711812 7.216048148428463 109 0 0 0.0 1.1763471100878191 2021-03-08 CENTRAL INDIA STORAGE 0.0 0 0 1080 Spring 92 3 92 4.477729048907452 5.043847129122387 121 0 0 0.0 1.193450710871694 2021-06-10 CENTRAL INDIA STORAGE 0.0 0 0 1054 Summer 91 0 73 4.401387684894597 3.148931390960325 99 0 0 0.0 1.0656484556598047 2021-06-21 WEST EUROPE COMPUTE 86116.0 106603 5823 0 Summer 97 0 81 2.0083494341316412 4.000211845980287 114 167218 82233 4.721948609439033 1.1696818578879498 2021-09-13 CENTRAL INDIA COMPUTE 176673.0 186228 6423 0 Autumn 95 3 102 3.4320958479577346 7.1402682714157955 106 96839 67794 160.60270820426587 1.1299617896607703 2021-12-17 WEST EUROPE COMPUTE 66129.0 79564 9042 0 Winter 89 1 70 5.918711066878549 7.229298099100743 107 133308 96481 -31.459043749546545 1.164868252435318 2021-12-28 CENTRAL INDIA COMPUTE 177873.0 200153 3669 0 Winter 84 1 76 4.146901687901895 4.711318109595819 99 52497 78989 125.187051361582 1.126661543766624 2022-01-08 CENTRAL INDIA STORAGE 0.0 0 0 754 Winter 100 0 69 2.658564336244997 7.425026982705308 95 0 0 0.0 1.147650639253864 2022-03-21 WEST EUROPE COMPUTE 148257.0 183418 5274 0 Spring 105 0 62 3.765290151370162 5.791612926264607 90 67466 141227 4.97780169514328 1.1254973418801169 2022-03-27 EAST US STORAGE 0.0 0 0 1046 Spring 101 0 60 2.091920418271799 7.559531625655739 103 0 0 0.0 1.1421202984755483 2022-04-23 CENTRAL INDIA COMPUTE 91497.0 107305 5074 0 Spring 108 0 91 4.213894990263793 5.303319070460034 129 151320 113256 -19.21222716677262 1.1

In [0]:
silver_master.groupBy("Service").count().show()



+-------+-----+
|Service|count|
+-------+-----+
|STORAGE| 5481|
|COMPUTE| 5481|
+-------+-----+

